# Project 3: Reddit Posts Classification

## Problem Statement


Classifying Reddit posts into their respective sub-reddits (in this case, Bitcoin and Ethereum) using Natural Language Processing. We will be training 2 models to determine which is more effective in its classification


## Executive Summary 

## Contents 

### Import Libraries 

In [1]:
# import statements 
import pandas as pd
import requests
import time
import random
import string
import nltk
import regex as re
import numpy as np
import matplotlib.pyplot as plt

from pprint import pprint
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from nltk.stem import WordNetLemmatizer

%matplotlib inline

In [2]:
pd.pandas.set_option('display.max_columns', None)

## 1. Extract Datasets From Reddit 

In [ ]:
url = 'https://www.reddit.com/r/bitcoin.json'

In [ ]:
def secret_agent_generator(N):
    return ''.join(random.choice(string.ascii_letters + string.digits) for _ in range(N))

### Bitcoin Subreddit 

In [ ]:
posts = []
after = None

for a in range(25):
    if after == None:
        current_url = url
    else:
        current_url = url + '?after=' + after
    print(current_url)
    res = requests.get(current_url, headers={'User-agent': secret_agent_generator(10)})
    
    if res.status_code != 200:
        print('Status error', res.status_code)
        break
    
    current_dict = res.json()
    current_posts = [p['data'] for p in current_dict['data']['children']]
    posts.extend(current_posts)
    after = current_dict['data']['after']
    
    # generate a random sleep duration to look more 'natural'
    sleep_duration = random.randint(2,60)
    print(sleep_duration)
    time.sleep(sleep_duration)

In [ ]:
pd.DataFrame(posts)

In [ ]:
df = pd.DataFrame(posts)
df

In [ ]:
columns_to_keep = ['title', 'selftext', 'subreddit',]

In [ ]:
# drop duplicate rows
df = df[columns_to_keep].drop_duplicates(subset=['selftext'])

In [ ]:
df[df["selftext"] == ""].shape

In [ ]:
df.drop(df[df["selftext"] == ""].index, inplace=True)

In [ ]:
# Create new column with title and selftext 
df['title_selftext'] = df['title'] + ' ' + df['selftext']

In [ ]:
df.reset_index
df

In [ ]:
df = df.drop(columns=['title', 'selftext'])
df

In [ ]:
df.to_csv('btc_data_raw.csv', index=False)

### Ethereum Subreddit

In [ ]:
url_2 = 'https://www.reddit.com/r/ethereum.json'

In [ ]:
eth_posts = []
after = None

for a in range(25):
    if after == None:
        current_url = url_2
    else:
        current_url = url_2 + '?after=' + after
    print(current_url)
    res = requests.get(current_url, headers={'User-agent': secret_agent_generator(10)})
    
    if res.status_code != 200:
        print('Status error', res.status_code)
        break
    
    current_dict = res.json()
    current_posts = [p['data'] for p in current_dict['data']['children']]
    eth_posts.extend(current_posts)
    after = current_dict['data']['after']
    
    # generate a random sleep duration to look more 'natural'
    sleep_duration = random.randint(2,60)
    print(sleep_duration)
    time.sleep(sleep_duration)

In [ ]:
eth_df = pd.DataFrame(eth_posts)
eth_df.head()

In [ ]:
eth_df.shape

In [ ]:
eth_df = eth_df[columns_to_keep]
eth_df.head()

In [ ]:
eth_df[eth_df['selftext'] == '']

In [ ]:
eth_df = eth_df.drop_duplicates(subset='selftext')
eth_df

In [ ]:
eth_df.drop(eth_df[eth_df["selftext"] == ""].index, inplace=True)

In [ ]:
eth_df

In [ ]:
eth_df['title_selftext'] = eth_df['title'] + ' ' + eth_df['selftext']
eth_df

In [ ]:
eth_df = eth_df.drop(columns=['title', 'selftext'])
eth_df.head()

In [ ]:
eth_df.to_csv("eth_raw", index=False)

## 2. Data Cleaning 


In [3]:
df = pd.read_csv('btc_data_raw.csv')

In [4]:
eth_df = pd.read_csv("eth_raw")

In [5]:
df_combined = pd.concat([df, eth_df],)
df_combined

subreddit                                     title_selftext
0     Bitcoin  Decentralization-Boosting Mining Protocol Stra...
1     Bitcoin  Daily Discussion, March 11, 2021 Please utiliz...
2     Bitcoin  I sold GME to buy bitcoin Why? Because the sto...
3     Bitcoin  BTC Art Asked a friend of mine who paints old ...
4     Bitcoin  Who else is dropping there 1400 dollar stimi i...
..        ...                                                ...
168  ethereum  What's happened to paper wallet creation? I'm ...
169  ethereum  Overview of EIP-2315 for Berlin upgrade by Gre...
170  ethereum  Noob question about transfer fees If I have an...
171  ethereum  A proposal for cross-rollup DEX (ethresear.ch)...
172  ethereum  What wallet do you use? I started with Coinbas...

[574 rows x 2 columns]

In [6]:
df_combined.shape

(574, 2)

In [7]:
# Assign 1 to Bitcoin, 0 to Ethereum
df_combined['subreddit'] = df_combined['subreddit'].map(lambda x: 1 if x == 'Bitcoin' else 0)
df_combined

subreddit                                     title_selftext
0            1  Decentralization-Boosting Mining Protocol Stra...
1            1  Daily Discussion, March 11, 2021 Please utiliz...
2            1  I sold GME to buy bitcoin Why? Because the sto...
3            1  BTC Art Asked a friend of mine who paints old ...
4            1  Who else is dropping there 1400 dollar stimi i...
..         ...                                                ...
168          0  What's happened to paper wallet creation? I'm ...
169          0  Overview of EIP-2315 for Berlin upgrade by Gre...
170          0  Noob question about transfer fees If I have an...
171          0  A proposal for cross-rollup DEX (ethresear.ch)...
172          0  What wallet do you use? I started with Coinbas...

[574 rows x 2 columns]

## 3. EDA 

## X. Preprocessing

In [15]:
from nltk.corpus import stopwords # Import the stopword list
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\Sir_A\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\Sir_A\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [16]:
def text_processing(raw_text):
    # Function to convert raw text to a string of words
    # 1. Remove non-letters.
    letters_only = re.sub("[^a-zA-Z]", " ", raw_text)
    
    # 2. Convert to lower case, split into individual words.
    words = letters_only.lower().split()
    
    # 3. Lemmatize 
    lemmatizer = WordNetLemmatizer()
    words_lem = [lemmatizer.lemmatize(i) for i in words]
    
    # 4. In Python, searching a set is much faster than searching
    # a list, so convert the stopwords to a set.
    stops = set(stopwords.words('english'))
    
    # 5. Remove stopwords.
    meaningful_words = [w for w in words_lem if w not in stops]
    
    # 6. Join the words back into one string separated by space, 
    # and return the result.
    return(" ".join(meaningful_words))

In [17]:
df_combined['title_selftext'] = df_combined['title_selftext'].map(text_processing)
df_combined['title_selftext']

0      decentralization boosting mining protocol stra...
1      daily discussion march please utilize sticky t...
2      sold gme buy bitcoin stock market decentralize...
3      btc art asked friend mine paint old weird decr...
4      else dropping dollar stimi bitcoin hello ha go...
                             ...                        
168    happened paper wallet creation cold storing bi...
169    overview eip berlin upgrade greg colvin peepan...
170    noob question transfer fee even number ethereu...
171    proposal cross rollup dex ethresear ch one cha...
172    wallet use started coinbase saw r coinbase tho...
Name: title_selftext, Length: 574, dtype: object

In [18]:
X = df_combined['title_selftext']
y = df_combined['subreddit']

In [19]:
# Split data into train and test sets
X_train, X_test, y_train, y_test = train_test_split(X, y, train_size=0.67, random_state=42, stratify=y)

## X. Classification Modelling 

In this section 

###  Baseline Accuracy

In [20]:
y.value_counts(normalize=True)

1    0.698606
0    0.301394
Name: subreddit, dtype: float64

### CountVectorizer with Logistic Regression Model (Baseline) 

In [38]:
# Stop words 
stop_words = set(stopwords.words('english'))  
additional_stop_words = ['bitcoin', 'btc', 'bit', 'ethereum', 'eth', 'ether']
stop_words = stop_words.union(additional_stop_words)

In [39]:
cvec = CountVectorizer(stop_words=stop_words)

In [40]:
X_train_transformed = cvec.fit_transform(X_train)
X_test_transformed = cvec.transform(X_test)

In [37]:
len(cvec.get_feature_names())

4457

In [41]:
X_train_df = pd.DataFrame(X_train_transformed.toarray(), columns=cvec.get_feature_names())
X_train_df

aab  aac  aave  aavvzcpu  ab  aback  abcdefg  abd  ability  able  \
0      0    0     0         0   0      0        0    0        0     0   
1      0    0     0         0   0      0        0    0        0     0   
2      0    0     0         0   0      0        0    0        0     0   
3      0    0     0         0   0      0        0    0        0     0   
4      0    0     0         0   0      0        0    0        0     0   
..   ...  ...   ...       ...  ..    ...      ...  ...      ...   ...   
379    0    0     0         0   0      0        0    0        0     0   
380    0    0     0         0   0      0        0    0        0     0   
381    0    0     0         0   1      0        0    0        0     0   
382    0    0     0         0   0      0        0    0        0     0   
383    0    0     0         0   0      0        0    0        0     0   

     absolutely  abstract  absurdly  abused  ac  aca  accelerate  accept  \
0             0         0         0       0   0    0           0       0   
1             0         0         0       0   0    0           0       0   
2             0         0         0       0   0    0           0       0   
3             0         0         0       0   0    0           0       0   
4             0         0         0       0   0    0           0       0   
..          ...       ...       ...     ...  ..  ...         ...     ...   
379           0         0         0       0   0    0           0       0   
380           0         0         0       0   0    0           0       0   
381           0         0         0       0   0    0           0       0   
382           0         0         0       0   0    0           0       0   
383           0         0         0       1   0    0           0       0   

     acceptable  accepted  accepting  access  accessed  accessibility  \
0             0         0          0       0         0              0   
1             0         0          0       0         0              0   
2             0         0          0       0         0              0   
3             0         0          0       0         0              0   
4             0         0          0       0         0              0   
..          ...       ...        ...     ...       ...            ...   
379           0         0          0       0         0              0   
380           0         0          0       0         0              0   
381           0         0          0       0         0              0   
382           0         0          0       0         0              0   
383           0         0          0       0         0              0   

     accessible  accident  accidentally  accomodation  accomplish  according  \
0             0         0             0             0           0          0   
1             0         0             0             0           0          0   
2             0         0             0             0           0          0   
3             0         0             0             0           0          0   
4             0         0             0             0           0          0   
..          ...       ...           ...           ...         ...        ...   
379           0         0             0             0           0          0   
380           0         0             0             0           0          0   
381           0         0             0             0           0          0   
382           0         0             0             0           0          0   
383           0         0             0             0           0          0   

     account  accreditation  accredited  accumulate  accuracy  accurate  \
0          0              0           0           0         0         0   
1          0              0           0           0         0         0   
2          0              0           0           0         0         0   
3          0              0           0           0         0         0   
4 

In [42]:
X_test_transformed = cvec.transform(X_test)
X_test_df = pd.DataFrame(X_test_transformed.toarray(), columns=cvec.get_feature_names())
X_test_df

aab  aac  aave  aavvzcpu  ab  aback  abcdefg  abd  ability  able  \
0      0    0     0         0   0      0        0    0        0     0   
1      0    0     0         0   0      0        0    0        0     0   
2      0    0     0         0   0      0        0    0        0     0   
3      0    0     0         0   0      0        0    0        0     0   
4      0    0     0         0   0      0        0    0        0     0   
..   ...  ...   ...       ...  ..    ...      ...  ...      ...   ...   
185    0    0     0         0   0      0        0    0        0     0   
186    0    0     0         0   0      0        0    0        0     0   
187    0    0     0         0   0      0        0    0        0     0   
188    0    0     0         0   0      0        0    0        0     0   
189    0    0     0         0   0      0        0    0        0     0   

     absolutely  abstract  absurdly  abused  ac  aca  accelerate  accept  \
0             0         0         0       0   0    0           0       0   
1             0         0         0       0   0    0           0       0   
2             0         0         0       0   0    0           0       0   
3             0         0         0       0   0    0           0       0   
4             0         0         0       0   0    0           0       0   
..          ...       ...       ...     ...  ..  ...         ...     ...   
185           0         0         0       0   0    0           0       0   
186           0         0         0       0   0    0           0       0   
187           0         0         0       0   0    0           0       0   
188           0         0         0       0   0    0           0       0   
189           0         0         0       0   0    0           0       0   

     acceptable  accepted  accepting  access  accessed  accessibility  \
0             0         0          0       2         0              0   
1             0         0          0       0         0              0   
2             0         0          0       0         0              0   
3             0         0          0       0         0              0   
4             0         0          0       0         0              0   
..          ...       ...        ...     ...       ...            ...   
185           0         0          0       0         0              0   
186           0         0          0       0         0              0   
187           0         0          0       0         0              0   
188           0         0          0       0         0              0   
189           0         0          0       0         0              0   

     accessible  accident  accidentally  accomodation  accomplish  according  \
0             0         0             0             0           0          0   
1             0         0             0             0           0          0   
2             0         0             0             0           0          0   
3             0         0             0             0           0          0   
4             0         0             0             0           0          0   
..          ...       ...           ...           ...         ...        ...   
185           0         0             0             0           0          0   
186           0         0             0             0           0          0   
187           0         0             0             0           0          0   
188           0         0             0             0           0          0   
189           0         0             0             0           0          0   

     account  accreditation  accredited  accumulate  accuracy  accurate  \
0          0              0           0           0         0         0   
1          0              0           0           0         0         0   
2          0              0           0           0         0         0   
3          0              0           0           0         0         0   
4 

In [ ]:
lr = LogisticRegression()
lr.fit(X_train_transformed, y_train)

print(f'Training Score: {lr.score(X_train_transformed, y_train)}')
print(f'Testing Score: {lr.score(X_test_transformed, y_test)}')

In [ ]:
cv_accuracies = cross_val_score(lr, X_train_transformed, y_train, cv=5).mean()
cv_accuracies

### Logistic Regression Model  

In [25]:
logr_model = Pipeline([
    ('cvec', CountVectorizer(stop_words=stop_words)),
    ('lr', LogisticRegression()),
    ('knn', KNeighborsClassifier()),
])

TypeError: All intermediate steps should be transformers and implement fit and transform or be the string 'passthrough' 'LogisticRegression()' (type <class 'sklearn.linear_model._logistic.LogisticRegression'>) doesn't

In [24]:
logr_pipe_params = {
    'cvec__max_features': [2000, 3000, 4000, 5000],
    'cvec__min_df': [2, 3], 
    'cvec__max_df': [0.9, 0.95], 
    'cvec__ngram_range': [(1,1), (1,2)], 
    ''
}

<bound method Pipeline.get_params of Pipeline(steps=[('cvec',
                 CountVectorizer(stop_words={'a', 'about', 'above', 'after',
                                             'again', 'against', 'ain', 'all',
                                             'am', 'an', 'and', 'any', 'are',
                                             'aren', "aren't", 'as', 'at', 'be',
                                             'because', 'been', 'before',
                                             'being', 'below', 'between', 'bit',
                                             'bitcoin', 'both', 'btc', 'but',
                                             'by', ...})),
                ('lr', LogisticRegression())])>

In [ ]:
y_test.value_counts(normalize=True)

In [ ]:
pipe_lr = Pipeline('lr')

### k Neighbors Classifier Model 

In [ ]:
knn = KNeighborsClassifier(n_neighbors=5)
knn.fit(X_train_transformed, y_train)

print(f'Training Score: {knn.score(X_train_transformed, y_train)}')
print(f'Testing Score: {knn.score(X_test_transformed, y_test)}')

In [ ]:
cv_accuracies = cross_val_score(knn, X_train_transformed, y_train, cv=5).mean()
cv_accuracies

In [ ]:
pipe.fit(X_train, y_train)

In [ ]:
pipe.score(X_train, y_train)

In [ ]:
pipe.score(X_test, y_test)

#### Hyperparameter tuning with GridSearchCV

In [ ]:
np.random.seed(42)

# try 2-NN, 3-NN
neighbors_to_test = [2, 3]

# try uniform and distance weightings.
weightings_to_test = ['uniform', 'distance']

# try Manhattan and Euclidean distances.
distance_metrics_to_test =  [1, 2]
# p = 1 is Manhattan, p = 2 is Euclidean

# Instantiate a dictionary to hold our accuracy scores.
accuracies = {}

# Loop through number of neighbors.
for k in neighbors_to_test: 
    # Loop through the weightings.
    for w in weightings_to_test:
        # Loop through our distance metrics.
        for d in distance_metrics_to_test:
            # Instantiate a kNN model with that set of hyperparameters.
            knn = KNeighborsClassifier(n_neighbors=k, weights=w, p=d)
            # Generate a set of accuracy scores based on 5-fold cross-validation.
            cv_accuracies = cross_val_score(knn, X_train, y_train, cv=5)   # to get a different metric, add scoring = 'neg_mean_...'
            # CVS gives accuracy here | unbiased estimate
            # Average the five accuracy scores and store them in the dictionary.
            accuracies[k, w, d] = cv_accuracies.mean()

# we want to find the model with the best metric for the data it has not yet seen 
accuracies

In [ ]:
knn_params = {
    'n_neighbors': range(1, 51, 5),
    'p': [1, 2],                                  # euclidean and manhatten distance 
    'weights' : ['uniform', 'distance']
}

In [ ]:
knn_gridsearch = GridSearchCV(KNeighborsClassifier(),
                             knn_params,
                             cv=5, 
                             verbose=1)

In [ ]:
knn_gridsearch.fit(X_train_transformed, y_train)

In [ ]:
print(f"The best parameters for kNN are: {knn_gridsearch.best_params_}")
print(f"The mean cross-validated score for the best kNN parameters is: {knn_gridsearch.best_score_}")
print(f"The mean test accuracy for kNN is: {knn_gridsearch.score(X_test_transformed, y_test)}")

In [ ]:
pd.DataFrame(knn_gridsearch.cv_results_).sort_values('rank_test_score')

#### Pipeline Hyperparameter Turning Using GridSearchCV

In [ ]:
pipe = Pipeline([('k_neighbors_step', KNeighborsClassifier(n_neighbors=5))])

In [ ]:
grid_param = ['classifier': [LogisticRegression()],
              'classifier__penalty'
                
]

### Naive Bayes Model 

## X. Evaluations & Recommendations